In [1]:
%matplotlib inline
import os
import re
import datetime as dt
import numpy as np
import pandas as pd

pd.set_option('precision', 3)

import matplotlib.pyplot as plt
from args_jupyter import args, createfolder
from meteorology import read_data, localP_2_seaP
from scipy.interpolate import Rbf
from mpl_toolkits.basemap import Basemap

In [2]:
print(args)
ty_list = pd.read_excel(args.ty_list)
sta_list = pd.read_excel(args.sta_list)
sta_list.set_index('NO', inplace=True)
sta_list.index = sta_list.index.astype(str)
print(ty_list.head())
print(sta_list.head())

{'study_area': 'Taipei', 'working_folder': '/home/jack/ssd/01_ty_research', 'I_y': [23.9125, 26.15], 'I_x': [120.4, 122.6375], 'F_y': [24.6625, 25.4], 'F_x': [121.15, 121.8875], 'O_y': [20, 27], 'O_x': [118, 123.5], 'res_degree': 0.0125, 'compression': 'bz2', 'figure_dpi': 150, 'RAD_cmap': ['#FFFFFF', '#FFD8D8', '#FFB8B8', '#FF9090', '#FF6060', '#FF2020', '#CC0000', '#A00000'], 'RAD_level': [-5, 0, 10, 20, 30, 40, 50, 60, 70], 'QPE_cmap': ['#FFFFFF', '#D2D2FF', '#AAAAFF', '#8282FF', '#6A6AFF', '#4242FF', '#1A1AFF', '#000090', '#000040', '#000030'], 'QPE_level': [-5, 0, 10, 20, 35, 50, 80, 120, 160, 200], 'QPF_cmap': ['#FFFFFF', '#D2D2FF', '#AAAAFF', '#8282FF', '#6A6AFF', '#4242FF', '#1A1AFF', '#000090', '#000040', '#000030'], 'QPF_level': [-5, 0, 10, 20, 35, 50, 80, 120, 160, 200], 'ty_list': '/home/jack/ssd/01_ty_research/ty_list.xlsx', 'sta_list': '/home/jack/ssd/01_ty_research/sta_list_all.xlsx', 'TW_map_file': '/home/jack/ssd/01_ty_research/07_gis_data/03_TW_shapefile/gadm36_TWN_2'

## Draw

In [47]:
timestep = ty_list['Time of canceling'] - ty_list['Time of issuing']

X, Y = np.meshgrid(args.xaxis_list, args.yaxis_list)

Xi, Yi = X.flatten(), Y.flatten()
fontsize = 7
m = Basemap(projection='cyl', resolution='h', llcrnrlat=args.F_y[0], 
            urcrnrlat=args.F_y[1], llcrnrlon=args.F_x[0], urcrnrlon=args.F_x[1])

for idx, i in enumerate(timestep[:1]):
    timelines = [ty_list['Time of issuing'][idx]+dt.timedelta(hours=x) for x in range(i.days*24+i.seconds//3600)][40:60]
    fig, ax = plt.subplots(len(timelines)//5, 5, dpi=args.figure_dpi*3, figsize=(20,20))
    data_man = os.path.join(args.rainfall_folder, 'UTF8', str(ty_list.iloc[idx,2].year)+'.Data', str(ty_list.iloc[idx,2].year)+'_Station_hr_man', 
                            ty_list.iloc[idx,1]+'.txt')
    data_auto = os.path.join(args.rainfall_folder, 'UTF8', str(ty_list.iloc[idx,2].year)+'.Data', str(ty_list.iloc[idx,2].year)+'_Station_hr_auto', 
                             ty_list.iloc[idx,1]+'.txt')
    data = read_data(data_man, data_auto, sta_list)
    
    for idj, j in enumerate(timelines):
        dd = ax[idj//5][idj%5]
        x = data.loc[j,'lon'].values
        y = data.loc[j,'lat'].values
#         z = data.loc[j,'PS01'].values
        z = localP_2_seaP(p=data.loc[j, 'PS01'].values, h=data.loc[j, 'height'].values, t=data.loc[j, 'TX01'].values)
        sci_IDW = Rbf(x, y, z, function='linear')
        Zi = sci_IDW(Xi, Yi).reshape(args.I_shape[0], args.I_shape[1])
        if 1:
            _ = m.readshapefile(args.TW_map_file, name='Taiwan', linewidth=0.25, drawbounds=True, color='k', ax=dd)
            m.plot(x, y,'.', color='k', markersize=1, ax=dd, label='Rain station')
            cs = m.contourf(x=X, y=Y, data=Zi, ax=dd)
            cbar = fig.colorbar(cs, ax=dd, fraction=0.2, shrink=0.7)
            cbar.ax.tick_params(labelsize=fontsize)
            
            dd.set_xlabel(r'longtitude($^o$)',fontdict={'fontsize':fontsize})
            dd.set_ylabel(r'latitude($^o$)',fontdict={'fontsize':fontsize})
            _ = dd.set_xticks(ticks = np.linspace(args.F_x[0], args.F_x[1], 5))
            _ = dd.set_yticks(ticks = np.linspace(args.F_y[0], args.F_y[1], 5))
            dd.tick_params('both', labelsize=fontsize)
            dd.locator_params(nbins=4)
            dd.legend(fontsize=fontsize)
            dd.set_title(j, fontsize=fontsize)
    fig.tight_layout()
    fig.subplots_adjust(wspace=0, hspace=0)

In [ ]:
timestep = ty_list['Time of canceling'] - ty_list['Time of issuing']

X, Y = np.meshgrid(args.xaxis_list, args.yaxis_list)
Xf, Yf = X.flatten(), Y.flatten()

column = pd.Index(args.xaxis_list,name='lon')
index = pd.Index(args.yaxis_list, decimals=4,name='lat')

for idx, i in enumerate(timestep):
    print(ty_list.iloc[idx,1])
    timelines = [ty_list['Time of issuing'][idx]+dt.timedelta(hours=x) for x in range(i.days*24+i.seconds//3600+1)]
    data_man = os.path.join(args.rainfall_folder, 'UTF8', str(ty_list.iloc[idx,2].year)+'.Data', str(ty_list.iloc[idx,2].year)+'_Station_hr_man', ty_list.iloc[idx,1]+'.txt')
    data_auto = os.path.join(args.rainfall_folder, 'UTF8', str(ty_list.iloc[idx,2].year)+'.Data', str(ty_list.iloc[idx,2].year)+'_Station_hr_auto', ty_list.iloc[idx,1]+'.txt')
    data = read_data(data_man, data_auto, sta_list)
    for j in range(len(timelines)-1):
        x1 = data.loc[timelines[j]].lon.values
        y1 = data.loc[timelines[j]].lat.values
        x2 = data.loc[timelines[j+1]].lon.values
        y2 = data.loc[timelines[j+1]].lat.values
        for k in data.columns[1:-3]:
            z1 = data.loc[timelines[j], k].values
            z2 = data.loc[timelines[j+1], k].values
            if k == 'PS01':
                z1 = localP_2_seaP(p=data.loc[timelines[j], k].values, h=data.loc[timelines[j], 'height'].values, 
                                   t=data.loc[timelines[j], 'TX01'].values)
                z2 = localP_2_seaP(p=data.loc[timelines[j+1], k].values, h=data.loc[timelines[j+1], 'height'].values, 
                                   t=data.loc[timelines[j+1], 'TX01'].values)
            
            sci_IDW_1 = Rbf(x1, y1, z1, function='linear')
            Z1 = sci_IDW_1(Xf, Yf).reshape(args.I_shape[0], args.I_shape[1])
            Z1[Z1 < 0] = 0
            Z1 = pd.DataFrame(Z1, columns=column, index=index)
            
            sci_IDW_2 = Rbf(x2, y2, z2, function='linear')
            Z2 = sci_IDW_2(Xf, Yf).reshape(args.I_shape[0], args.I_shape[1])
            Z2[Z2 < 0] = 0
            Z2 = pd.DataFrame(Z2, columns=column, index=index)
            
            createfolder(os.path.join(args.wrangled_rainfall_folder, str(timelines[j].year)+'.'+ty_list.iloc[idx,1]))
            
            for i in range(7):
                Z = Z1+(Z2-Z1)*i/5
                output_path = os.path.join(args.wrangled_rainfall_folder, str(timelines[j].year)+'.'+ty_list.iloc[idx,1], 
                                           k+'.{}.pkl'.format(dt.datetime.strftime(timelines[j]+dt.timedelta(minutes=10*i), format='%Y%m%d%H%M')))
                Z.to_pickle(output_path, compression=args.compression)

SAOLA
SOULIK
TRAMI
KONG-REY
USAGI
FITOW
MATMO
CHAN-HOM
SOUDELOR
